In [8]:
import ultralytics
from ultralytics import YOLO
from PIL import Image
import cv2

model = YOLO("yolov8m.pt").cuda()

In [39]:
import os
import argparse

import cv2

output_dir = './output'
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

def process_img(img, model: ultralytics.models.yolo.model.YOLO):
    H, W, _ = img.shape

    img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    
    out = model.predict(source=img_rgb, save=False, verbose=False)

    if len(out) != 0:
        for o in out:
            bbox = o.boxes.xywhn.tolist()[0]

            x1, y1, w, h = bbox[0], bbox[1], bbox[2], bbox[3]

            x1 = int((x1 - w/2) * W)
            y1 = int((y1 - h/2) * H)
            w = int(w * W)
            h = int(h * H)
            
            # print(x1, y1, w, h)
            # print(W, H)

            img[y1:y1 + h, x1:x1 + w, :] = cv2.blur(img[y1:y1 + h, x1:x1 + w, :], (30, 30))
                
    return img

In [40]:
filePath = "/workspace/Senegal vs Netherlands FIFA World Cup 2022 Group A (ITV Full Match HD)_Trim (2).mp4"
cap = cv2.VideoCapture(filePath)
ret, frame = cap.read()

output_video = cv2.VideoWriter(os.path.join(output_dir, 'output_detect_human.mp4'),
                               cv2.VideoWriter_fourcc(*'MP4V'),
                               25,
                               (frame.shape[1], frame.shape[0]))
i = 0

while ret:
    frame = process_img(frame, model)

    output_video.write(frame)

    ret, frame = cap.read()

    print(i)
    i += 1
    if i == 1000:
        break

cap.release()
output_video.release()

OpenCV: FFMPEG: tag 0x5634504d/'MP4V' is not supported with codec id 12 and format 'mp4 / MP4 (MPEG-4 Part 14)'
OpenCV: FFMPEG: fallback to use tag 0x7634706d/'mp4v'


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27